In [ ]:
!pip install --upgrade pandas==2.2.2

In [ ]:
!pip install --upgrade --force-reinstall numpy scipy
!pip install --upgrade --force-reinstall TTS

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 62.0/62.0 kB 1.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 62.0/62.0 kB 1.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 16.4/16.4 MB 33.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 37.6/37.6 MB 12.5 MB/s eta 0:00:00
  Attempting uninstall: numpy
    Found existing installation: numpy 2.0.2
    Uninstalling numpy-2.0.2:
      Successfully uninstalled numpy-2.0.2
  Attempting uninstall: scipy
    Found existing installation: scipy 1.14.1
    Uninstalling scipy-1.14.1:
      Successfully uninstalled scipy-1.14.1
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
numba 0.60.0 requires numpy<2.1,>=1.22, but you have numpy 2.2.4 which is incompatible.
tensorflow 2.18.0 requires numpy<2.1.0,>=1.26.0, but you have numpy 2.2.4 which is incompatible.
  Using cached scipy-1.

In [ ]:
!pip install fastapi uvicorn pyngrok TTS python-multipart



   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 94.9/94.9 kB 3.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 62.3/62.3 kB 4.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 72.0/72.0 kB 4.8 MB/s eta 0:00:00


In [ ]:
%%writefile main.py
from fastapi import FastAPI, UploadFile, File, Form
from fastapi.responses import FileResponse
from TTS.api import TTS
import uvicorn
import os
from pyngrok import ngrok

app = FastAPI()

# Load the multilingual voice cloning model globally.
tts_model = TTS(model_name="tts_models/multilingual/multi-dataset/your_tts")

# Set the default speaker WAV file path.
# Make sure this file is in your Colab environment.
DEFAULT_SPEAKER_PATH = "/content/default_speaker.wav"

@app.post("/tts")
async def generate_tts(
    text: str = Form(...),
    language: str = Form("en"),
    speaker_wav: UploadFile = File(None)
):
    """
    Endpoint: POST /tts
      - text: The text to synthesize.
      - language: Language code (e.g., "en" or "fr").
      - speaker_wav: Optional speaker audio file.
    """
    # Save the uploaded speaker file if provided; otherwise, use the default.
    if speaker_wav is not None:
        speaker_path = f"/tmp/{speaker_wav.filename}"
        with open(speaker_path, "wb") as f:
            content = await speaker_wav.read()
            f.write(content)
    else:
        speaker_path = DEFAULT_SPEAKER_PATH

    # Define an output file path.
    output_file = f"/tmp/output_{language}.wav"

    # Generate the TTS audio file.
    tts_model.tts_to_file(
        text=text,
        speaker_wav=speaker_path,
        language=language,
        file_path=output_file
    )

    # Return the generated audio file.
    return FileResponse(output_file, media_type="audio/wav", filename=os.path.basename(output_file))

if __name__ == "__main__":
    port = 8000
    # Open an ngrok tunnel to the local server.
    public_url = ngrok.connect(port).public_url
    print(f"ngrok tunnel: {public_url} -> http://127.0.0.1:{port}")
    uvicorn.run(app, host="0.0.0.0", port=port)


Writing main.py


In [ ]:
from google.colab import files
files.upload()  # Upload your default speaker file (e.g., default_speaker.wav)


Saving WhatsApp-Audio-2025-03-22-at-21.08.56-_1_.wav to WhatsApp-Audio-2025-03-22-at-21.08.56-_1_.wav


{'WhatsApp-Audio-2025-03-22-at-21.08.56-_1_.wav': b'RIFF\xee\x94\x0f\x00WAVEfmt \x10\x00\x00\x00\x01\x00\x01\x00D\xac\x00\x00\x88X\x01\x00\x02\x00\x10\x00LIST\xc2\x00\x00\x00INFOIART\x13\x00\x00\x00101soundboards.com\x00\x00ICMT\x13\x00\x00\x00101soundboards.com\x00\x00ICOP\x13\x00\x00\x00101soundboards.com\x00\x00IGNR\x07\x00\x00\x00Speech\x00\x00INAM\x13\x00\x00\x00101soundboards.com\x00\x00IPRD\x13\x00\x00\x00101soundboards.com\x00\x00IPRT\x04\x00\x00\x001/1\x00ISFT\x0e\x00\x00\x00Lavf58.76.100\x00data\x00\x94\x0f\x00\x94\xff\x83\xff\xc2\xff\xbf\xff\x93\xff\xac\xff\x0c\x00w\x00\xa6\x00\x8b\x00\x7f\x00\x87\x00D\x00\xd7\xff\x91\xffh\xffS\xffY\xffw\xff\xb3\xff\xf6\xff*\x00~\x00\xe2\x00\xf8\x00\xc7\x00\x91\x00Y\x00\x18\x00\xe4\xff\xc7\xff\xb2\xff\x9e\xff\xa7\xff\xce\xff\xe0\xff\xd8\xff\xdb\xff\xe0\xff\xf3\xff\x18\x00*\x00T\x00\xb6\x00\xda\x00\x97\x00X\x00.\x00\xf7\xff\xc6\xff\xaa\xff\xbf\xff\x08\x00>\x00W\x00s\x00x\x00p\x00l\x00X\x00G\x00\x1a\x00\xd8\xff\x14\x00X\x00\xd0\xff\xa4\xffe\x0

In [ ]:
!pip install fastapi uvicorn pyngrok TTS python-multipart



In [ ]:
%%writefile main.py
import time
import os
from fastapi import FastAPI, UploadFile, File, Form
from fastapi.responses import FileResponse
from fastapi.middleware.cors import CORSMiddleware
from TTS.api import TTS
import uvicorn
from pyngrok import ngrok

app = FastAPI()

# -----------------------------
# Enable CORS for all origins.
# In production, specify only your domain in allow_origins.
# -----------------------------
app.add_middleware(
    CORSMiddleware,
    allow_origins=["*"],  # e.g., ["http://127.0.0.1:5500"]
    allow_credentials=True,
    allow_methods=["*"],
    allow_headers=["*"],
)

# Load the TTS model once globally
tts_model = TTS(model_name="tts_models/multilingual/multi-dataset/your_tts")

# Default speaker WAV (update if you have a different path/file)
DEFAULT_SPEAKER_PATH = "/content/default_speaker.wav"

@app.post("/tts")
async def generate_tts(
    text: str = Form(...),
    language: str = Form("en"),
    speaker_wav: UploadFile = File(None)
):
    """
    POST /tts
    - text: The text to be synthesized.
    - language: Language code (e.g., "en" or "fr").
    - speaker_wav: Optional file upload for custom speaker audio.
    """
    # Save the uploaded speaker file if provided; otherwise, use default
    if speaker_wav is not None:
        speaker_path = f"/tmp/{speaker_wav.filename}"
        with open(speaker_path, "wb") as f:
            content = await speaker_wav.read()
            f.write(content)
    else:
        speaker_path = DEFAULT_SPEAKER_PATH

    # Output file for generated TTS
    output_file = f"/tmp/output_{language}.wav"

    # Generate TTS audio
    tts_model.tts_to_file(
        text=text,
        speaker_wav=speaker_path,
        language=language,
        file_path=output_file
    )

    # Optional: Wait briefly to ensure the file is fully written
    time.sleep(1)

    # Return the generated audio file
    return FileResponse(
        output_file,
        media_type="audio/wav",
        filename=os.path.basename(output_file)
    )

if __name__ == "__main__":
    # Expose on port 8000
    port = 8000
    # Create an ngrok tunnel
    public_url = ngrok.connect(port).public_url
    print(f"ngrok tunnel: {public_url} -> http://127.0.0.1:{port}")
    # Start the server
    uvicorn.run(app, host="0.0.0.0", port=port)


Overwriting main.py


In [ ]:
!python main.py

 > tts_models/multilingual/multi-dataset/your_tts is already downloaded.
 > Using model: vits
 > Setting up Audio Processor...
 | > sample_rate:16000
 | > resample:False
 | > num_mels:80
 | > log_func:np.log10
 | > min_level_db:0
 | > frame_shift_ms:None
 | > frame_length_ms:None
 | > ref_level_db:None
 | > fft_size:1024
 | > power:None
 | > preemphasis:0.0
 | > griffin_lim_iters:None
 | > signal_norm:None
 | > symmetric_norm:None
 | > mel_fmin:0
 | > mel_fmax:None
 | > pitch_fmin:None
 | > pitch_fmax:None
 | > spec_gain:20.0
 | > stft_pad_mode:reflect
 | > max_norm:1.0
 | > clip_norm:True
 | > do_trim_silence:False
 | > trim_db:60
 | > do_sound_norm:False
 | > do_amp_to_db_linear:True
 | > do_amp_to_db_mel:True
 | > do_rms_norm:False
 | > db_level:None
 | > stats_path:None
 | > base:10
 | > hop_length:256
 | > win_length:1024
 > Model fully restored. 
 > Setting up Audio Processor...
 | > sample_rate:16000
 | > resample:False
 | > num_mels:64
 | > log_func:np.log10
 | > min_level_db:-

In [ ]:
# Print the dictionary of supported languages
print(tts.languages) # Use tts.languages to get supported languages
# Use tts.supported_languages to get supported languages

NameError: name 'tts' is not defined

In [ ]:

from pyngrok import ngrok

# Set your ngrok authtoken
ngrok.set_auth_token("2uhxbejq6iUflYv7CzkuxZnTEbQ_2dWqBrumk4Su1ZfAntRmH")

# Open a tunnel on port 8000
public_url = ngrok.connect(8000)
print("Public URL:", public_url)


Public URL: NgrokTunnel: "https://c98b-35-229-157-112.ngrok-free.app" -> "http://localhost:8000"


In [ ]:
 %%writefile backend.py
from fastapi import FastAPI, File, UploadFile, Form, BackgroundTasks, HTTPException
from fastapi.responses import FileResponse, JSONResponse
import os
import uuid
from TTS.api import TTS

app = FastAPI()

# Load the multilingual voice cloning model once at startup
tts = TTS(model_name="tts_models/multilingual/multi-dataset/your_tts")

# Allowed language options
ALLOWED_LANGUAGES = ['en', 'fr-fr', 'pt-br']

@app.post("/synthesize")
async def synthesize(
    background_tasks: BackgroundTasks,
    text: str = Form(..., description="Text to synthesize"),
    language: str = Form(..., description="Language code (options: 'en', 'fr-fr', 'pt-br')"),
    speaker_wav: UploadFile = File(..., description="WAV file for voice cloning")
):
    if language not in ALLOWED_LANGUAGES:
        raise HTTPException(
            status_code=400,
            detail=f"Invalid language. Please choose one of {ALLOWED_LANGUAGES}"
        )

    temp_speaker_file = f"temp_{uuid.uuid4().hex}.wav"
    with open(temp_speaker_file, "wb") as f:
        f.write(await speaker_wav.read())

    output_file = f"output_{uuid.uuid4().hex}.wav"

    try:
        tts.tts_to_file(
            text=text,
            speaker_wav=temp_speaker_file,
            language=language,
            file_path=output_file
        )
    except Exception as e:
        return JSONResponse(status_code=500, content={"error": str(e)})
    finally:
        os.remove(temp_speaker_file)

    background_tasks.add_task(os.remove, output_file)

    return FileResponse(
        path=output_file,
        filename="synthesized.wav",
        media_type="audio/wav",
        headers={"Content-Disposition": "attachment; filename=synthesized.wav"}
    )

if __name__ == "__main__":
    import uvicorn
    uvicorn.run(app, host="0.0.0.0", port=8000)


In [ ]:
!pip install pyngrok